In [1]:
import pandas as pd
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from sklearn.linear_model import LinearRegression
import pytz
import datetime

In [2]:
import warnings
warnings.filterwarnings('ignore')

# Import et nettoyage #

In [3]:
df_source = pd.read_csv(
    "sources/consommation-quotidienne-brute.csv", 
    delimiter=";",
    )

In [4]:
df_source.tail(1)

Date - Heure        Date  Heure  \
192862  2012-01-01T00:00:00+01:00  01/01/2012  00:00   

        Consommation brute gaz (MW PCS 0°C) - GRTgaz Statut - GRTgaz  \
192862                                       52099.0       Définitif   

        Consommation brute gaz (MW PCS 0°C) - Teréga Statut - Teréga  \
192862                                        3254.0       Définitif   

        Consommation brute gaz totale (MW PCS 0°C)  \
192862                                     55353.0   

        Consommation brute électricité (MW) - RTE Statut - RTE  \
192862                                    59610.0    Définitif   

        Consommation brute totale (MW)  
192862                        114963.0

In [5]:
df_energie = df_source.drop(columns=[
    "Date","Heure",
    "Consommation brute gaz (MW PCS 0°C) - GRTgaz",
    "Statut - GRTgaz","Consommation brute gaz (MW PCS 0°C) - Teréga",
    "Statut - Teréga"])

In [6]:
df_energie.columns=["Date","Conso_gaz_totale_MW","Conso_elec_totale_MW","Statut","Conso_brute_totale_MW"]

In [7]:
# Convertit la colonne date au format Str. 
# utc n'est que True ou False
df_energie["Date"] = pd.to_datetime(df_energie["Date"], utc=True)
# On repasse donc en heure FR
df_energie["Date"] = df_energie["Date"].dt.tz_convert('Europe/Paris')

In [8]:
# Les données sont en ordre décroissant, les plus récentes en 1er.
# On se replace en ordre chronologique
df_energie.sort_values(by=["Date"], ascending=True, inplace=True)
df_energie.reset_index(drop=True, inplace=True)

In [9]:
# passage de la colonne date en index
df_energie.set_index('Date', inplace=True)

In [10]:
# Les mesures de ce Dataset sont arrêtées au 31/05/2022
df_energie = df_energie.loc [ df_energie.index < "2022-06-01" ]

In [11]:
df_energie["Conso_gaz_totale_MW"] = df_energie["Conso_gaz_totale_MW"].interpolate(method='linear', axis=0)
df_energie["Conso_brute_totale_MW"] = df_energie["Conso_brute_totale_MW"].interpolate(method='linear', axis=0)

In [12]:
df_energie.head()

Conso_gaz_totale_MW  Conso_elec_totale_MW  \
Date                                                                   
2012-01-01 00:00:00+01:00              55353.0               59610.0   
2012-01-01 00:30:00+01:00              55398.5               58314.0   
2012-01-01 01:00:00+01:00              55444.0               56230.0   
2012-01-01 01:30:00+01:00              55454.5               56075.0   
2012-01-01 02:00:00+01:00              55465.0               55531.0   

                              Statut  Conso_brute_totale_MW  
Date                                                         
2012-01-01 00:00:00+01:00  Définitif               114963.0  
2012-01-01 00:30:00+01:00  Définitif               113318.5  
2012-01-01 01:00:00+01:00  Définitif               111674.0  
2012-01-01 01:30:00+01:00  Définitif               111335.0  
2012-01-01 02:00:00+01:00  Définitif               110996.0

In [13]:
# Vérification que plus aucune ligne n'est vide
df_energie.isna().sum()

Conso_gaz_totale_MW      0
Conso_elec_totale_MW     0
Statut                   0
Conso_brute_totale_MW    0
dtype: int64

In [14]:
print("Nombre de lignes sur la période 2012-2022 : ",df_energie.shape[0])

Nombre de lignes sur la période 2012-2022 :  182592


# Moyenne mobile #

In [15]:
rolling_max_7j = df_energie["Conso_elec_totale_MW"].rolling(
    window=336,       # Moyenne mobile Hebdo (48x30mn x 7j)
    center=True,      
    min_periods=168,  # débute à la moitié de la fenêtre définie
).max()

In [16]:
df_energie["MA_max_7j"] = rolling_max_7j

# Visualisation #

In [17]:
df_energie.describe()

Conso_gaz_totale_MW  Conso_elec_totale_MW  Conso_brute_totale_MW  \
count        182592.000000         182592.000000          182592.000000   
mean          54018.475664          54144.101330          108160.623171   
std           28978.525136          12022.053534           40087.315950   
min            1877.000000          28738.000000           45476.000000   
25%           28523.000000          44998.000000           74817.000000   
50%           47047.750000          52510.000000           97884.000000   
75%           76023.125000          62412.000000          138092.625000   
max          176040.000000         101866.000000          274815.000000   

           MA_max_7j  
count  182592.000000  
mean    65628.655927  
std     11786.136991  
min     47454.000000  
25%     55643.000000  
50%     61956.000000  
75%     75572.000000  
max    101866.000000

In [18]:
df_last_3y = df_energie.loc[ df_energie.index >= '2018-08-01' ]

In [19]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=df_last_3y.index, y=df_last_3y["Conso_elec_totale_MW"],
                    mode='markers',
                    name='Mesures brutes',
                    marker_color=df_last_3y["Conso_elec_totale_MW"],
                    marker=dict(
                        opacity=0.1,
                        size=2)
                        )
             )

fig.add_trace(go.Scatter(x=df_last_3y.index, y=df_last_3y["MA_max_7j"],
                    mode='lines',
                    name='Moy. Mobile Max hebdo')
             )

fig.update_layout(title='Consommation electrique en MW depuis 2018 en France')

fig.show()

# Export #

In [20]:
df_energie.to_csv("sources/1_conso_energies_raff.csv",header=True, index=True)